<a href="https://colab.research.google.com/github/Dr-Isam-ALJAWARNEH/ds-project-thematic-maps/blob/main/code/stratified_sampling_RMSE_PM2_5_NYC.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
!pip install polygeohasher
!pip install folium
!pip install uszipcode
%pip install pygeohash
!pip install geopandas

  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.1/1.1 MB 7.1 MB/s eta 0:00:00
  Created wheel for geohash: filename=Geohash-1.0-py3-none-any.whl size=15521 sha256=960180eec1b9baf6cd628a6a96e81e125a36b00135283b9c2b4d4e986ee79624
  Stored in directory: /root/.cache/pip/wheels/48/25/c0/7e05d2e26b685459182eb8519d42edb6c3a02a3ccb81ea6653
Successfully built geohash
  Attempting uninstall: geopandas
    Found existing installation: geopandas 0.13.2
    Uninstalling geopandas-0.13.2:
      Successfully uninstalled geopandas-0.13.2
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 57.0/57.0 kB 4.4 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 59.9/59.9 kB 7.9 MB/s eta 0:00:00
  Created wheel for atomicwrites: filename=atomicwrites-1.4.1-py2.py3-none-any.whl size=6941 sha256=e843bc5043dea32def55830eacdecdd683f1febdc69955af71756b2c766a39f3
  Stored in directory: /root/.cache/pip/wheels/34/07/0b/33b15f68

In [2]:
'''from google.colab import drive
drive.mount('/content/drive')'''

"from google.colab import drive\ndrive.mount('/content/drive')"

In [3]:
from pandas import Series, DataFrame
import pandas as pd
import numpy as np
import plotly.graph_objs as go
from IPython.display import Image
import folium
from folium import IFrame
from folium.plugins import MarkerCluster
from folium import plugins
from datetime import datetime
import datetime as dt
import json
from scipy import stats
import pygeohash as gh
import geopandas as gpd

import os

In [4]:
sampling_fraction = 0.8
geohash_precision = 6

In [5]:
air =  pd.read_csv('https://raw.githubusercontent.com/IsamAljawarneh/datasets/master/data/NYC_PM.csv')
air.head()

SensorID        time   latitude  longitude  bin0  bin1  bin2  bin3  bin4  \
0  NYCP1_01A  1579618560  40.847183 -73.870087    23     1     2     0     0   
1  NYCP1_01A  1579618560  40.847183 -73.870094    18     2     1     0     0   
2  NYCP1_01A  1579618560  40.847179 -73.870094    18     1     0     0     0   
3  NYCP1_01A  1579618560  40.847179 -73.870094    18     1     2     0     0   
4  NYCP1_01A  1579618560  40.847179 -73.870094    20     3     0     2     2   

   bin5  ...  bin19  bin20  bin21  bin22  bin23  temperature  humidity   pm1  \
0     0  ...    0.0    0.0    0.0    0.0    0.0         16.3      15.2  1.44   
1     0  ...    0.0    0.0    0.0    0.0    0.0         16.2      15.1  1.05   
2     0  ...    0.0    0.0    0.0    0.0    0.0         16.1      15.1  0.74   
3     0  ...    0.0    0.0    0.0    0.0    0.0         16.1      15.2  1.15   
4     0  ...    0.0    0.0    0.0    0.0    0.0         16.0      15.2  2.13   

   pm25   pm10  
0  5.91  11.35  
1  1.18   1.18  
2  0.76   0.76  
3  4.48  47.36  
4  5.77   6.18  

[5 rows x 33 columns]

In [6]:
'''air =  pd.read_csv('/content/drive/MyDrive/foundation_of_DS/project/Data/NYC_air_quality_1.csv')
air.head()'''

"air =  pd.read_csv('/content/drive/MyDrive/foundation_of_DS/project/Data/NYC_air_quality_1.csv')\nair.head()"

In [7]:
air = \
air[(air['latitude'] != 0 ) & \
(air['longitude']!=0 )]

In [8]:
%%time
air['geohash']=air.apply(lambda x: gh.encode(x.latitude, x.longitude, precision=geohash_precision), axis=1)

CPU times: user 6.03 s, sys: 148 ms, total: 6.18 s
Wall time: 7.86 s


In [9]:
# convert to Geopandas Geodataframe
%%time
#join with geojson polygons to calculate RMSE
gdf_air = gpd.GeoDataFrame(air,   geometry=gpd.points_from_xy(air.longitude, air.latitude))

CPU times: user 189 ms, sys: 9.89 ms, total: 199 ms
Wall time: 266 ms


In [10]:
gdf_air.shape

(118765, 35)

In [11]:
#simple random sampling (SRS)
#gdf_air=gdf_air.sample(frac=sampling_fraction)

In [12]:
gdf_air.shape

(118765, 35)

In [13]:
hoods = gpd.read_file("https://raw.githubusercontent.com/IsamAljawarneh/datasets/master/data/nyc_polygon.geojson")
hoods.head()

neighborhood boroughCode        borough  \
0         Allerton           2          Bronx   
1  Alley Pond Park           4         Queens   
2    Arden Heights           5  Staten Island   
3        Arlington           5  Staten Island   
4         Arrochar           5  Staten Island   

                                                 @id  \
0  http://nyc.pediacities.com/Resource/Neighborho...   
1  http://nyc.pediacities.com/Resource/Neighborho...   
2  http://nyc.pediacities.com/Resource/Neighborho...   
3  http://nyc.pediacities.com/Resource/Neighborho...   
4  http://nyc.pediacities.com/Resource/Neighborho...   

                                            geometry  
0  POLYGON ((-73.84860 40.87167, -73.84582 40.870...  
1  POLYGON ((-73.74333 40.73888, -73.74371 40.739...  
2  POLYGON ((-74.16983 40.56108, -74.16982 40.561...  
3  POLYGON ((-74.15975 40.64142, -74.15998 40.641...  
4  POLYGON ((-74.06078 40.59319, -74.06079 40.593...

In [14]:
'''hoods = gpd.read_file("/content/drive/MyDrive/foundation_of_DS/project/Data/nyc_polygon.geojson")
hoods.head()'''

'hoods = gpd.read_file("/content/drive/MyDrive/foundation_of_DS/project/Data/nyc_polygon.geojson")\nhoods.head()'

generate geohash for each tuple (long, lat) as well as convert both trips and polygons to GeoPandas

In [15]:
hoods['geometry'] = hoods.geometry.to_crs("epsg:3857")
#hoods['geometryn'] = hoods.geometry.to_crs("epsg:3857")
hoods

neighborhood boroughCode        borough  \
0           Allerton           2          Bronx   
1    Alley Pond Park           4         Queens   
2      Arden Heights           5  Staten Island   
3          Arlington           5  Staten Island   
4           Arrochar           5  Staten Island   
..               ...         ...            ...   
305  Windsor Terrace           3       Brooklyn   
306        Woodhaven           4         Queens   
307         Woodlawn           2          Bronx   
308          Woodrow           5  Staten Island   
309         Woodside           4         Queens   

                                                   @id  \
0    http://nyc.pediacities.com/Resource/Neighborho...   
1    http://nyc.pediacities.com/Resource/Neighborho...   
2    http://nyc.pediacities.com/Resource/Neighborho...   
3    http://nyc.pediacities.com/Resource/Neighborho...   
4    http://nyc.pediacities.com/Resource/Neighborho...   
..                                                 ...   
305  http://nyc.pediacities.com/Resource/Neighborho...   
306  http://nyc.pediacities.com/Resource/Neighborho...   
307  http://nyc.pediacities.com/Resource/Neighborho...   
308  http://nyc.pediacities.com/Resource/Neighborho...   
309  http://nyc.pediacities.com/Resource/Neighborho...   

                                              geometry  
0    POLYGON ((-8220788.214 4993431.406, -8220479.3...  
1    POLYGON ((-8209070.244 4973902.938, -8209112.6...  
2    POLYGON ((-8256547.374 4947814.753, -8256546.8...  
3    POLYGON ((-8255425.402 4959593.695, -8255451.0...  
4    POLYGON ((-8244408.305 4952520.907, -8244409.6...  
..                                                 ...  
305  POLYGON ((-8235422.696 4962430.807, -8235402.3...  
306  POLYGON ((-8222316.990 4967599.072, -8221672.8...  
307  POLYGON ((-8221998.344 4997679.030, -8221975.2...  
308  POLYGON ((-8257377.292 4944818.936, -8257371.5...  
309  POLYGON ((-8226606.801 4976664.013, -8226525.9...  

[310 rows x 5 columns]

In [16]:
gdf_air = gdf_air.set_crs('epsg:4326')
gdf_air['geometry'] = gdf_air.geometry.to_crs("epsg:3857")
gdf_air['geometryn'] = gdf_air.geometry.to_crs("epsg:3857")
gdf_air

SensorID        time   latitude  longitude  bin0  bin1  bin2  bin3  \
0       NYCP1_01A  1579618560  40.847183 -73.870087    23     1     2     0   
1       NYCP1_01A  1579618560  40.847183 -73.870094    18     2     1     0   
2       NYCP1_01A  1579618560  40.847179 -73.870094    18     1     0     0   
3       NYCP1_01A  1579618560  40.847179 -73.870094    18     1     2     0   
4       NYCP1_01A  1579618560  40.847179 -73.870094    20     3     0     2   
...           ...         ...        ...        ...   ...   ...   ...   ...   
118760  NYCP1_01A  1581033300  40.819511 -73.898369    40     6     0     0   
118761  NYCP1_01A  1581033300  40.819511 -73.898369    48     2     1     1   
118762  NYCP1_01A  1581033300  40.819511 -73.898369     0     0     0     0   
118763  NYCP1_01A  1581033300  40.819511 -73.898369    37     1     0     0   
118764  NYCP1_01A  1581033300  40.819511 -73.898369    39     2     2     0   

        bin4  bin5  ...  bin22  bin23  temperature  humidity   pm1  pm25  \
0          0     0  ...    0.0    0.0         16.3      15.2  1.44  5.91   
1          0     0  ...    0.0    0.0         16.2      15.1  1.05  1.18   
2          0     0  ...    0.0    0.0         16.1      15.1  0.74  0.76   
3          0     0  ...    0.0    0.0         16.1      15.2  1.15  4.48   
4          2     0  ...    0.0    0.0         16.0      15.2  2.13  5.77   
...      ...   ...  ...    ...    ...          ...       ...   ...   ...   
118760     0     0  ...    0.0    0.0         14.0      86.0  3.91  4.03   
118761     0     0  ...    0.0    0.0         14.0      86.1  4.87  6.15   
118762     0     0  ...    0.0    0.0         14.1      86.0  0.00  0.00   
118763     0     0  ...    0.0    0.0         13.9      86.4  2.45  2.49   
118764     2     0  ...    0.0    0.0         13.9      86.3  4.63  9.82   

         pm10  geohash                          geometry  \
0       11.35   dr72rh  POINT (-8223180.470 4989827.255)   
1        1.18   dr72rh  POINT (-8223181.249 4989827.255)   
2        0.76   dr72rh  POINT (-8223181.249 4989826.666)   
3       47.36   dr72rh  POINT (-8223181.249 4989826.666)   
4        6.18   dr72rh  POINT (-8223181.249 4989826.666)   
...       ...      ...                               ...   
118760   4.03   dr72nq  POINT (-8226328.808 4985755.918)   
118761   6.20   dr72nq  POINT (-8226328.808 4985755.918)   
118762   0.00   dr72nq  POINT (-8226328.808 4985755.918)   
118763   2.49   dr72nq  POINT (-8226328.808 4985755.918)   
118764  10.49   dr72nq  POINT (-8226328.808 4985755.918)   

                               geometryn  
0       POINT (-8223180.470 4989827.255)  
1       POINT (-8223181.249 4989827.255)  
2       POINT (-8223181.249 4989826.666)  
3       POINT (-8223181.249 4989826.666)  
4       POINT (-8223181.249 4989826.666)  
...                                  ...  
118760  POINT (-8226328.808 4985755.918)  
118761  POINT (-8226328.808 4985755.918)  
118762  POINT (-8226328.808 4985755.918)  
118763  POINT (-8226328.808 4985755.918)  
118764  POINT (-8226328.808 4985755.918)  

[118765 rows x 36 columns]

In [17]:
%%time
#BASELINE
# we join by sjoin, but we have geohash so, we sample stratified by geohash
# so, we join only to get the metrics but the stratified sampling is based on the fine-grained division (geohash in this case)
sjoined_air_original = gpd.sjoin(gdf_air, hoods, predicate="within")
sjoined_air_original.head(2)

CPU times: user 534 ms, sys: 73.1 ms, total: 607 ms
Wall time: 1.25 s


SensorID        time   latitude  longitude  bin0  bin1  bin2  bin3  bin4  \
0  NYCP1_01A  1579618560  40.847183 -73.870087    23     1     2     0     0   
1  NYCP1_01A  1579618560  40.847183 -73.870094    18     2     1     0     0   

   bin5  ...  pm25   pm10  geohash                          geometry  \
0     0  ...  5.91  11.35   dr72rh  POINT (-8223180.470 4989827.255)   
1     0  ...  1.18   1.18   dr72rh  POINT (-8223181.249 4989827.255)   

                          geometryn  index_right  neighborhood  boroughCode  \
0  POINT (-8223180.470 4989827.255)           38    Bronx Park            2   
1  POINT (-8223181.249 4989827.255)           38    Bronx Park            2   

   borough                                                @id  
0    Bronx  http://nyc.pediacities.com/Resource/Neighborho...  
1    Bronx  http://nyc.pediacities.com/Resource/Neighborho...  

[2 rows x 41 columns]

In [18]:
n = len(pd.unique(sjoined_air_original['neighborhood']))

print("No.of.unique name values :", n)

No.of.unique name values : 60


In [19]:
sjoined_air_original.shape

(118495, 41)

In [20]:
%%time
# this is the NEW method that we want to compare with (in your case sample by H3 or Google's S2)
# sampling by geohash change fraction above (sampling rate) (20%, 40%, 60%, 80%)
sampled_geohash_data= sjoined_air_original.groupby('geohash').apply(lambda x: x.sample(frac=sampling_fraction))

CPU times: user 976 ms, sys: 5.19 ms, total: 981 ms
Wall time: 1.25 s


In [21]:
sampled_geohash_data.shape

(94791, 41)

generate h3 cell for each tuple (long, lat) as well as convert both trips and polygons to GeoPandas

In [22]:
!pip install h3

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.2/1.2 MB 9.0 MB/s eta 0:00:00


In [23]:
import h3

In [24]:
air.shape

(118765, 34)

In [25]:
H3_res = 10

def geo_2_h3(row):
  return h3.geo_to_h3(lat=float(row.latitude),lng=float(row.longitude),resolution = H3_res)

In [26]:
%%time
sjoined_air_original['h3_cell'] = sjoined_air_original.apply(geo_2_h3,axis=1)

CPU times: user 3.66 s, sys: 132 ms, total: 3.79 s
Wall time: 4.54 s


In [27]:
air_sample_pcount = (sjoined_air_original
                          .groupby('h3_cell')
                          .pm25
                          .agg(list)
                          .to_frame("ids")
                          .reset_index())
# No. points inside the hexagon
air_sample_pcount['count'] =(air_sample_pcount['ids']
                      .apply(lambda pm25_ids:len(pm25_ids)))
air_sample_pcount.shape

(1261, 3)

In [28]:
air_sample_pcount.sort_values('count',ascending=False)

h3_cell                                                ids  count
516  8a2a100a9157fff  [0.46, 1.79, 6.63, 2.1, 1.2, 1.2, 0.07, 0.81, ...  10514
190  8a2a1001321ffff  [5.91, 1.18, 0.76, 4.48, 5.77, 0.73, 1.22, 4.5...   8517
188  8a2a1001320ffff  [0.71, 0.04, 2.74, 1.13, 2.24, 2.71, 2.92, 2.4...   6821
123  8a2a100126dffff  [0.2, 0.0, 0.1, 0.55, 0.28, 1.67, 1.8, 4.11, 7...   3792
205  8a2a100132effff  [1.98, 1.39, 3.44, 5.74, 1.42, 5.87, 3.03, 1.4...   3659
..               ...                                                ...    ...
179  8a2a1001311ffff                                             [0.31]      1
194  8a2a10013247fff                                             [0.39]      1
213  8a2a1001334ffff                                             [1.88]      1
238  8a2a10013b4ffff                                             [0.84]      1
685  8a2a100ac127fff                                             [3.45]      1

[1261 rows x 3 columns]

In [29]:
air_sample_pcount

h3_cell                                                ids  \
0     8a2a10002447fff  [11.56, 7.11, 7.11, 31.82, 2.12, 1.89, 3.07, 1...   
1     8a2a10002457fff  [56.05, 60.47, 37.68, 15.38, 24.34, 7.82, 0.9,...   
2     8a2a1000245ffff                               [8.89, 17.79, 14.46]   
3     8a2a10002467fff      [82.26, 10.67, 13.44, 3.01, 3.47, 3.47, 4.01]   
4     8a2a100024c7fff                                       [1.12, 1.74]   
...               ...                                                ...   
1256  8a2a1072dc67fff                                 [0.45, 0.45, 0.23]   
1257  8a2a1072dc6ffff                                        [0.0, 0.06]   
1258  8a2a1072dcc7fff                     [0.45, 0.91, 1.13, 0.03, 0.03]   
1259  8a2a1072dcdffff                     [0.91, 0.45, 0.06, 0.45, 0.06]   
1260  8a2a1072dceffff          [0.45, 0.68, 1.13, 0.06, 0.0, 0.06, 0.05]   

      count  
0         8  
1         9  
2         3  
3         7  
4         2  
...     ...  
1256      3  
1257      2  
1258      5  
1259      5  
1260      7  

[1261 rows x 3 columns]

In [30]:
air_sample_ncount = (sjoined_air_original
                          .groupby('h3_cell')
                          .neighborhood
                          .agg(list)
                          .to_frame("ids")
                          .reset_index())
# No. points inside the hexagon
air_sample_ncount['count'] =(air_sample_ncount['ids']
                      .apply(lambda neighborhood_ids:len(neighborhood_ids)))
air_sample_ncount.shape

(1261, 3)

In [31]:
air_sample_ncount

h3_cell                                                ids  \
0     8a2a10002447fff  [Pelham Bay Park, Pelham Bay Park, Pelham Bay ...   
1     8a2a10002457fff  [Pelham Bay Park, Pelham Bay Park, Pelham Bay ...   
2     8a2a1000245ffff  [Pelham Bay Park, Pelham Bay Park, Pelham Bay ...   
3     8a2a10002467fff  [Pelham Bay Park, Pelham Bay Park, Pelham Bay ...   
4     8a2a100024c7fff                 [Pelham Bay Park, Pelham Bay Park]   
...               ...                                                ...   
1256  8a2a1072dc67fff  [Lower East Side, Lower East Side, Lower East ...   
1257  8a2a1072dc6ffff                 [Lower East Side, Lower East Side]   
1258  8a2a1072dcc7fff  [Lower East Side, Lower East Side, Lower East ...   
1259  8a2a1072dcdffff  [Lower East Side, Lower East Side, Lower East ...   
1260  8a2a1072dceffff  [Lower East Side, Lower East Side, Lower East ...   

      count  
0         8  
1         9  
2         3  
3         7  
4         2  
...     ...  
1256      3  
1257      2  
1258      5  
1259      5  
1260      7  

[1261 rows x 3 columns]

In [32]:
%%time
# this is the NEW method that we want to compare with (in your case sample by H3 or Google's S2)
# sampling by geohash change fraction above (sampling rate) (20%, 40%, 60%, 80%)
sampled_geohash_data= sjoined_air_original.groupby('geohash').apply(lambda x: x.sample(frac=sampling_fraction))

CPU times: user 929 ms, sys: 9.79 ms, total: 939 ms
Wall time: 1.07 s


In [33]:
%%time
#BASELINE: original ==> this is the baseline we compare with, all data where sampling fraction =100, resembles  `without sampling`
geohash_data_original = sjoined_air_original.groupby('geohash').apply(lambda x: x.sample(frac=1))

CPU times: user 1.03 s, sys: 13.2 ms, total: 1.04 s
Wall time: 1.25 s


In [34]:
%%time
# this is the NEW method that we want to compare with (in your case sample by H3 or Google's S2)
# sampling by geohash change fraction above (sampling rate) (20%, 40%, 60%, 80%)
sampled_h3_data= sjoined_air_original.groupby('h3_cell').apply(lambda x: x.sample(frac=sampling_fraction))

CPU times: user 6.67 s, sys: 72.6 ms, total: 6.74 s
Wall time: 10.4 s


In [35]:
sampled_h3_data.shape

(94801, 42)

In [36]:
sampled_geohash_data.shape

(94791, 42)

Not really applicable to the H3 Uber, as it summarizes datapoint based on location rather than sample them.

In [37]:
# sampled data scenario #2
sampled_geohash_data2= sampled_geohash_data['neighborhood'].value_counts()
sampled_geohash_data2 = sampled_geohash_data2.reset_index()
sampled_geohash_data2.columns = ['neighborhood','count']
sampled_geohash_data2['neighborhood'] = sampled_geohash_data2['neighborhood'].astype(str)

In [38]:
# original data
geohash_data_original2= geohash_data_original['neighborhood'].value_counts()
geohash_data_original2 = geohash_data_original2.reset_index()
geohash_data_original2.columns = ['neighborhood','count']
geohash_data_original2['neighborhood'] = geohash_data_original2['neighborhood'].astype(str)

In [39]:
# sampled data scenario #2
sampled_h3_data2= sampled_h3_data['neighborhood'].value_counts() #h3_cell
sampled_h3_data2 = sampled_h3_data2.reset_index()
sampled_h3_data2.columns = ['neighborhood','count']
sampled_h3_data2['neighborhood'] = sampled_h3_data2['neighborhood'].astype(str)

In [40]:
sampled_h3_data2.head(6)

neighborhood  count
0     Longwood  31533
1  Hunts Point  18905
2   Bronx Park  17444
3     Van Nest   5507
4      Fordham   4094
5       Harlem   2547

In [41]:
sampled_geohash_data2.head(6)

neighborhood  count
0     Longwood  31553
1  Hunts Point  18880
2   Bronx Park  17436
3     Van Nest   5502
4      Fordham   4093
5       Harlem   2547

In [42]:
geohash_data_original2.head(6)

neighborhood  count
0     Longwood  39426
1  Hunts Point  23625
2   Bronx Park  21819
3     Van Nest   6862
4      Fordham   5111
5       Harlem   3184

In [43]:
#reference geo-map
geohash_data_original2["neighborhood"].astype(str)
heatmap_scale = list()
threshold = [10,20,50,70,85,100]
for i in threshold :
    heatmap_scale.append(int(geohash_data_original2['count'].max() * (i/100.0)))

map_geohash_data_original2 = folium.Map(location=[40.730610, -73.935242], zoom_start=10)
map_geohash_data_original2.choropleth(geo_data=hoods, data=geohash_data_original2, \
                data_out = 'nyc_zip_test.json',
             columns=['neighborhood', 'count'],
             #threshold_scale= heatmap_scale,
             key_on='feature.properties.neighborhood',
             fill_color='YlOrRd', fill_opacity=0.9, line_opacity=0.9,nan_fill_color='white',
             legend_name='Number of Pickups')

/usr/local/lib/python3.10/dist-packages/folium/folium.py:465: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  warnings.warn(


In [44]:
map_geohash_data_original2

In [45]:
#NEW sampling geo-map
sampled_geohash_data2["neighborhood"].astype(str)
heatmap_scale = list()
threshold = [10,20,50,70,85,100]
for i in threshold :
    heatmap_scale.append(int(sampled_geohash_data2['count'].max() * (i/100.0)))

map_sampled_geohash_data2 = folium.Map(location=[40.730610, -73.935242], zoom_start=10)
map_sampled_geohash_data2.choropleth(geo_data=hoods, data=sampled_geohash_data2, \
                data_out = 'nyc_zip_test.json',
             columns=['neighborhood', 'count'],
             #threshold_scale= heatmap_scale,
             key_on='feature.properties.neighborhood',
             fill_color='YlOrRd', fill_opacity=0.9, line_opacity=0.9,nan_fill_color='white',
             legend_name='Number of Pickups')

/usr/local/lib/python3.10/dist-packages/folium/folium.py:465: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  warnings.warn(


In [46]:
map_sampled_geohash_data2

In [47]:
#NEW sampling geo-map
sampled_h3_data2["neighborhood"].astype(str)
heatmap_scale = list()
threshold = [10,20,50,70,85,100]
for i in threshold :
    heatmap_scale.append(int(sampled_h3_data2['count'].max() * (i/100.0)))

map_sampled_h3_data2 = folium.Map(location=[40.730610, -73.935242], zoom_start=10)
map_sampled_h3_data2.choropleth(geo_data=hoods, data=sampled_h3_data2, \
                data_out = 'nyc_zip_test.json',
             columns=['neighborhood', 'count'],
             #threshold_scale= heatmap_scale,
             key_on='feature.properties.neighborhood',
             fill_color='YlOrRd', fill_opacity=0.9, line_opacity=0.9,nan_fill_color='white',
             legend_name='Number of Pickups')

/usr/local/lib/python3.10/dist-packages/folium/folium.py:465: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  warnings.warn(


In [48]:
map_sampled_h3_data2

In [49]:
geohash_data_original["centroid"] = geohash_data_original["geometryn"].centroid
geohash_data_original.head(1)

SensorID        time  latitude  longitude  bin0  bin1  bin2  \
geohash                                                                        
dr5ref  105484  NYCP1_01A  1580906040  40.70977 -74.004745    28     1     1   

                bin3  bin4  bin5  ...  geohash  \
geohash                           ...            
dr5ref  105484     1     2     0  ...   dr5ref   

                                        geometry  \
geohash                                            
dr5ref  105484  POINT (-8238170.530 4969626.598)   

                                       geometryn  index_right  \
geohash                                                         
dr5ref  105484  POINT (-8238170.530 4969626.598)           97   

                      neighborhood  boroughCode    borough  \
geohash                                                      
dr5ref  105484  Financial District            1  Manhattan   

                                                              @id  \
geohash                                                             
dr5ref  105484  http://nyc.pediacities.com/Resource/Neighborho...   

                        h3_cell                          centroid  
geohash                                                            
dr5ref  105484  8a2a10728957fff  POINT (-8238170.530 4969626.598)  

[1 rows x 43 columns]

In [50]:
geohash_data_original['otherNAME'] = geohash_data_original['neighborhood']
geohash_data_original.head(1)

SensorID        time  latitude  longitude  bin0  bin1  bin2  \
geohash                                                                        
dr5ref  105484  NYCP1_01A  1580906040  40.70977 -74.004745    28     1     1   

                bin3  bin4  bin5  ...                          geometry  \
geohash                           ...                                     
dr5ref  105484     1     2     0  ...  POINT (-8238170.530 4969626.598)   

                                       geometryn  index_right  \
geohash                                                         
dr5ref  105484  POINT (-8238170.530 4969626.598)           97   

                      neighborhood  boroughCode    borough  \
geohash                                                      
dr5ref  105484  Financial District            1  Manhattan   

                                                              @id  \
geohash                                                             
dr5ref  105484  http://nyc.pediacities.com/Resource/Neighborho...   

                        h3_cell                          centroid  \
geohash                                                             
dr5ref  105484  8a2a10728957fff  POINT (-8238170.530 4969626.598)   

                         otherNAME  
geohash                             
dr5ref  105484  Financial District  

[1 rows x 44 columns]

In [51]:
geohash_data_original["centroid"] = geohash_data_original["geometryn"].centroid
geohash_data_original.head(1)

SensorID        time  latitude  longitude  bin0  bin1  bin2  \
geohash                                                                        
dr5ref  105484  NYCP1_01A  1580906040  40.70977 -74.004745    28     1     1   

                bin3  bin4  bin5  ...                          geometry  \
geohash                           ...                                     
dr5ref  105484     1     2     0  ...  POINT (-8238170.530 4969626.598)   

                                       geometryn  index_right  \
geohash                                                         
dr5ref  105484  POINT (-8238170.530 4969626.598)           97   

                      neighborhood  boroughCode    borough  \
geohash                                                      
dr5ref  105484  Financial District            1  Manhattan   

                                                              @id  \
geohash                                                             
dr5ref  105484  http://nyc.pediacities.com/Resource/Neighborho...   

                        h3_cell                          centroid  \
geohash                                                             
dr5ref  105484  8a2a10728957fff  POINT (-8238170.530 4969626.598)   

                         otherNAME  
geohash                             
dr5ref  105484  Financial District  

[1 rows x 44 columns]

In [52]:
## ALTERNATIVE : Group by geohash
%%time
data_original_grouped = geohash_data_original[['otherNAME','centroid','neighborhood','geometry','pm25']].groupby(['neighborhood'], as_index=False).agg({'otherNAME':'first','neighborhood': 'count', 'centroid':'first' ,'geometry':'first','pm25':'first'})


CPU times: user 124 ms, sys: 5.83 ms, total: 130 ms
Wall time: 152 ms


In [53]:
sampled_geohash_data['otherNAME'] = sampled_geohash_data['neighborhood']

In [54]:
%%time
# EMD
sampled_geohash_data["centroid"] = sampled_geohash_data["geometryn"].centroid

CPU times: user 61.9 ms, sys: 1.92 ms, total: 63.8 ms
Wall time: 66.4 ms


In [55]:
## ALTERNATIVE: Group by geohash
%time

sampled_geohash_grouped = sampled_geohash_data[['otherNAME','geometry','neighborhood','centroid','pm25']].groupby(['neighborhood'], as_index=False).agg({'otherNAME':'first','neighborhood': 'count', 'centroid':'first', 'geometry': 'first','pm25':'first'})


CPU times: user 5 µs, sys: 0 ns, total: 5 µs
Wall time: 9.06 µs


In [56]:
# 3857 is the projected CRS of Shenzhen china, while 4326 is the geographic CRS. Here we need the projected CRS for centroid
%%time

sampled_geohash_grouped  = gpd.GeoDataFrame(sampled_geohash_grouped, crs="EPSG:3857", geometry=sampled_geohash_grouped.geometry)
sampled_geohash_grouped.head()

CPU times: user 7.61 ms, sys: 915 µs, total: 8.52 ms
Wall time: 8.47 ms


otherNAME  neighborhood                          centroid  \
0    Allerton            11  POINT (-8223033.528 4991310.584)   
1     Astoria           239  POINT (-8228541.171 4976594.708)   
2     Belmont           176  POINT (-8224783.916 4989658.317)   
3  Bronx Park         17436  POINT (-8223708.681 4989014.970)   
4   Bronxdale           429  POINT (-8222893.377 4990515.542)   

                           geometry   pm25  
0  POINT (-8223033.528 4991310.584)   0.38  
1  POINT (-8228541.171 4976594.708)   0.81  
2  POINT (-8224783.916 4989658.317)  48.69  
3  POINT (-8223708.681 4989014.970)  22.64  
4  POINT (-8222893.377 4990515.542)   0.43

In [57]:
sampled_h3_data['otherNAME'] = sampled_h3_data['neighborhood']

In [58]:
%%time
# EMD
sampled_h3_data["centroid"] = sampled_h3_data["geometryn"].centroid

CPU times: user 251 ms, sys: 11 ms, total: 262 ms
Wall time: 368 ms


In [59]:
## ALTERNATIVE: Group by geohash
%time

sampled_h3_grouped = sampled_h3_data[['otherNAME','geometry','neighborhood','centroid','pm25']].groupby(['neighborhood'], as_index=False).agg({'otherNAME':'first','neighborhood': 'count', 'centroid':'first', 'geometry': 'first','pm25':'first'})


CPU times: user 3 µs, sys: 0 ns, total: 3 µs
Wall time: 6.91 µs


In [60]:
# 3857 is the projected CRS of Shenzhen china, while 4326 is the geographic CRS. Here we need the projected CRS for centroid
%%time

sampled_h3_grouped  = gpd.GeoDataFrame(sampled_h3_grouped, crs="EPSG:3857", geometry=sampled_h3_grouped.geometry)
sampled_h3_grouped.head()

CPU times: user 6.68 ms, sys: 982 µs, total: 7.66 ms
Wall time: 11 ms


otherNAME  neighborhood                          centroid  \
0    Allerton            10  POINT (-8223008.926 4991312.203)   
1     Astoria           239  POINT (-8229083.074 4979219.908)   
2     Belmont           177  POINT (-8224625.953 4991401.984)   
3  Bronx Park         17444  POINT (-8223221.213 4994360.220)   
4   Bronxdale           416  POINT (-8221706.934 4991345.908)   

                           geometry  pm25  
0  POINT (-8223008.926 4991312.203)  0.24  
1  POINT (-8229083.074 4979219.908)  0.00  
2  POINT (-8224625.953 4991401.984)  0.74  
3  POINT (-8223221.213 4994360.220)  0.10  
4  POINT (-8221706.934 4991345.908)  1.50

In [61]:
#INNER JOIN to calibrate both distributions: drop rows in original that do not have match in NEW reduced version
data_original_grouped1 = pd.merge(data_original_grouped,sampled_geohash_data,on=["otherNAME"],suffixes=('', '_y'))
data_original_grouped1.drop(data_original_grouped1.filter(regex='_y$').columns, axis=1, inplace=True)
#type(data_original_grouped)


This cell causes the entire session to reset

In [62]:
#INNER JOIN to calibrate both distributions: drop rows in GeoRAP that do not have match in base version

#sampled_geohash_data = pd.merge(sampled_geohash_data,data_original_grouped1,on=["otherNAME"],suffixes=('', '_y'))
#sampled_geohash_data.drop(sampled_geohash_data.filter(regex='_y$').columns, axis=1, inplace=True)

#type(sampled_data_grouped)

In [63]:
#INNER JOIN to calibrate both distributions: drop rows in original that do not have match in NEW reduced version
data_original_grouped2 = pd.merge(data_original_grouped,sampled_h3_grouped,on=["otherNAME"],suffixes=('', '_y'))
data_original_grouped2.drop(data_original_grouped2.filter(regex='_y$').columns, axis=1, inplace=True)
#type(data_original_grouped)


This cell causes the entire session to reset

In [64]:
#INNER JOIN to calibrate both distributions: drop rows in GeoRAP that do not have match in base version

#sampled_h3_data = pd.merge(sampled_h3_data,data_original_grouped2,on=["otherNAME"],suffixes=('', '_y'))
#sampled_h3_data.drop(sampled_h3_data.filter(regex='_y$').columns, axis=1, inplace=True)

#type(sampled_data_grouped)

In [65]:
#extract column count neighborhood to numpy array
count_original = data_original_grouped['neighborhood'].to_numpy()
#count_original
#extract column average Trip_distance to numpy array
average_original = data_original_grouped['pm25'].to_numpy()
#average_original

In [66]:
# you need to normalize so that all add up to one
count_original = count_original/count_original.sum()
#count_original

In [67]:
# to numpy array
count_scenario2 = sampled_geohash_data['neighborhood'].to_numpy()
#count_scenario2
# to numpy array
average_scenario2 = sampled_geohash_data['pm25'].to_numpy()
#average_scenario2


error

In [68]:
# Ensure numeric values
#if count_scenario2.dtype == 'object':
    # Convert to numeric type (e.g., int or float)
 #   count_scenario2 = pd.to_numeric(count_scenario2, errors='coerce')

#count_scenario2 = count_scenario2/count_scenario2.sum()
#count_scenario2

In [69]:
# to numpy array
count_scenario3 = sampled_h3_data['neighborhood'].to_numpy()
#count_scenario2
# to numpy array
average_scenario3 = sampled_h3_data['pm25'].to_numpy()
#average_scenario2

error

In [70]:
# Ensure numeric values
#if count_scenario3.dtype == 'object':
    # Convert to numeric type (e.g., int or float)
 #   count_scenario3 = pd.to_numeric(count_scenario3, errors='coerce')

#count_scenario3 = count_scenario3/count_scenario3.sum()
#count_scenario3

#MAPE

In [71]:
#Defining MAPE function
def MAPE(Y_actual,Y_Predicted):
    mape = np.mean(np.abs((Y_actual - Y_Predicted)/Y_actual))*100
    return mape

In [72]:
# to numpy array - groupby geohash instead
count_scenario2 = sampled_geohash_data['geohash'].to_numpy()
count_scenario2

array(['dr5ref', 'dr5ref', 'dr5ref', ..., 'dr7882', 'dr7882', 'dr7882'],
      dtype=object)

In [73]:
# to numpy array - groupby geohash instead
count_scenario3 = sampled_h3_data['h3_cell'].to_numpy()
count_scenario3

array(['8a2a10002447fff', '8a2a10002447fff', '8a2a10002447fff', ...,
       '8a2a1072dceffff', '8a2a1072dceffff', '8a2a1072dceffff'],
      dtype=object)

In [ ]:
MAPE(count_original,count_scenario2)

In [75]:
#MAPE(average_original,average_scenario2)

In [76]:
#MAPE(count_original,count_scenario3)

In [77]:
#MAPE(average_original,average_scenario3)

In [78]:
data_original_grouped  = gpd.GeoDataFrame(data_original_grouped, crs="EPSG:3857", geometry=data_original_grouped.geometry)

In [79]:
%%time
data_original_grouped.sort_values('neighborhood',ascending=False).head(2)

CPU times: user 6.73 ms, sys: 0 ns, total: 6.73 ms
Wall time: 7 ms


otherNAME  neighborhood                          centroid  \
26     Longwood         39426  POINT (-8226744.141 4984763.941)   
22  Hunts Point         23625  POINT (-8226047.726 4984671.868)   

                            geometry  pm25  
26  POINT (-8226744.141 4984763.941)  4.94  
22  POINT (-8226047.726 4984671.868)  3.29

In [80]:
sampled_geohash_data['otherNAME'] = sampled_geohash_data['neighborhood']

#RMSE

In [81]:
#Defining RMSE function
def RMSE(Y_actual,Y_Predicted):
    rmse = np.sqrt(1/np.count_nonzero(Y_actual) * np.sum(np.power(Y_actual - Y_Predicted,2)))
    return rmse

In [ ]:
#%%time
#RMSE
RMSE(count_original,count_scenario2)

In [83]:
#%%time
#RMSE
#RMSE(count_original,count_scenario3)

Spearman correlation coefficient

In [84]:
# Assuming count_original has a shape of (48,) and count_scenario3 has a shape of (136003,)
if count_original.shape[0] < count_scenario2.shape[0]:
    count_scenario2 = np.resize(count_scenario2, (count_original.shape[0],))
else:
    count_original = np.resize(count_original, (count_scenario2.shape[0],))


In [85]:
# Assuming count_original has a shape of (48,) and count_scenario3 has a shape of (136003,)
if count_original.shape[0] < average_scenario2.shape[0]:
    average_scenario2 = np.resize(average_scenario2, (count_original.shape[0],))
else:
    count_original = np.resize(count_original, (average_scenario2.shape[0],))


In [86]:
# Assuming count_original has a shape of (48,) and count_scenario3 has a shape of (136003,)
if count_original.shape[0] < count_scenario3.shape[0]:
    count_scenario3 = np.resize(count_scenario3, (count_original.shape[0],))
else:
    count_original = np.resize(count_original, (count_scenario3.shape[0],))


In [87]:
# Assuming count_original has a shape of (48,) and average_scenario3 has a shape of (136003,)
if count_original.shape[0] < average_scenario3.shape[0]:
    average_scenario3 = np.resize(average_scenario3, (count_original.shape[0],))
else:
    count_original = np.resize(count_original, (average_scenario3.shape[0],))


geohash

In [88]:
res = stats.spearmanr(count_original, count_scenario2)
res.statistic

0.1102626117318192

In [89]:
res = stats.spearmanr(average_original, average_scenario2)
res.statistic

0.037139959239839766

h3

In [90]:
res = stats.spearmanr(count_original, count_scenario3)
res.statistic

-0.04034991789620243

In [91]:
res = stats.spearmanr(count_original, average_scenario3)
res.statistic

-0.19481421812600747

Minkowski distance

geohash

In [92]:
from scipy.spatial import distance
#distance.minkowski(count_scenario2,count_original, 1)


In [93]:

distance.minkowski(average_original,average_scenario2, 1)

431.56999999999994

h3

In [94]:
#distance.minkowski(count_scenario3,count_original, 1)

In [95]:
distance.minkowski(average_original,average_scenario3, 1)

1019.68

Kullback–Leibler divergence

geohash

In [96]:
from scipy.special import rel_entr

#calculate (P || Q)
#sum(rel_entr(count_scenario2, count_original))

In [97]:
#calculate (P || Q)
sum(rel_entr(average_original,average_scenario2))

1005.0904667351392

h3

In [98]:
#calculate (P || Q)
#sum(rel_entr(count_scenario3, count_original))

In [99]:
#calculate (P || Q)
sum(rel_entr(average_original,average_scenario3))

inf

jensenshannon

geohash

In [100]:
from scipy.spatial import distance
#distance.jensenshannon(count_scenario2, count_original)

In [101]:
distance.jensenshannon(average_original,average_scenario2)

0.565106995250252

h3

In [102]:
#distance.jensenshannon(count_scenario3, count_original)

In [103]:
distance.jensenshannon(average_original,average_scenario3)

0.6392888743109213

All commented errors are a result of this error
TypeError: unsupported operand type(s) for /: 'str' and 'str'